In [1]:
import requests
from bs4 import BeautifulSoup
import csv
import os

# Créer le dossier 'scrap' s'il n'existe pas déjà
if not os.path.exists('scrap'):
    os.makedirs('scrap')

# Chemin du fichier CSV dans le dossier 'scrap'
csv_file_path = os.path.join('scrap', 'ebooks.csv')

# URL de la page des livres les plus populaires
url = "https://gutenberg.org/browse/scores/top"

# Faire une requête GET pour récupérer le contenu de la page
response = requests.get(url)

# Vérifier si la requête est réussie
if response.status_code == 200:
    # Parser le contenu HTML avec BeautifulSoup
    soup = BeautifulSoup(response.content, 'html.parser')
    
    # Trouver la balise <ol> qui contient les <li> des ebooks populaires
    ol_tag = soup.find('ol')
    
    # Ouvrir un fichier CSV en mode écriture dans le dossier 'scrap'
    with open(csv_file_path, mode='w', newline='', encoding='utf-8') as file:
        writer = csv.writer(file)
        # Écrire l'en-tête du fichier CSV
        writer.writerow(['Title', 'Link'])
        
        # Si la balise <ol> est trouvée
        if ol_tag:
            # Extraire tous les éléments <li> contenant des balises <a>
            for li_tag in ol_tag.find_all('li'):
                a_tag = li_tag.find('a')
                if a_tag:
                    title = a_tag.text
                    link = "https://gutenberg.org" + a_tag['href']
                    # Écrire chaque titre et lien dans le fichier CSV
                    writer.writerow([title, link])
        else:
            print("Aucune balise <ol> trouvée sur la page.")
else:
    print(f"Erreur lors de la récupération de la page : {response.status_code}")


In [2]:
import pandas as pd
df = pd.read_csv("scrap/ebooks.csv")
df

Title  \
0   Frankenstein; Or, The Modern Prometheus by Mar...   
1           Pride and Prejudice by Jane Austen (2835)   
2      Romeo and Juliet by William Shakespeare (2678)   
3   Moby Dick; Or, The Whale by Herman Melville (2...   
4    The Scarlet Letter by Nathaniel Hawthorne (2378)   
..                                                ...   
95  White Nights and Other Stories by Fyodor Dosto...   
96                   Peter Pan by J. M.  Barrie (353)   
97        Josefine Mutzenbacher by Felix Salten (352)   
98  A Military Dictionary and Gazetteer by Thomas ...   
99             The Time Machine by H. G.  Wells (344)   

                                  Link  
0      https://gutenberg.org/ebooks/84  
1    https://gutenberg.org/ebooks/1342  
2    https://gutenberg.org/ebooks/1513  
3    https://gutenberg.org/ebooks/2701  
4   https://gutenberg.org/ebooks/25344  
..                                 ...  
95  https://gutenberg.org/ebooks/36034  
96     https://gutenberg.org/ebooks/16  
97  https://gutenberg.org/ebooks/31284  
98  https://gutenberg.org/ebooks/59563  
99     https://gutenberg.org/ebooks/35  

[100 rows x 2 columns]

In [6]:
import pandas as pd
import requests
from bs4 import BeautifulSoup

# Load the CSV file containing links
df = pd.read_csv('scrap/ebooks.csv')

# Initialize the lists to store data
authors = []
titles = []
summaries = []
languages = []
subjects = []




# Iterate through each link in the DataFrame
for index, row in df.iterrows():
    link = row['Link']
    

    response = requests.get(link)
    soup = BeautifulSoup(response.content, 'html.parser')

    # Extract the required fields
    try:
        author = soup.find('th', string='Author').find_next('td').get_text(strip=True)
        title = soup.find('th', string='Title').find_next('td').get_text(strip=True)
        summary = soup.find('th', string='Summary').find_next('td').get_text(strip=True)
        language = soup.find('th', string='Language').find_next('td').get_text(strip=True)
        subject_tags = soup.find_all('th', string='Subject')
        subject_list = [tag.find_next('td').get_text(strip=True) for tag in subject_tags]
        subjects.append(", ".join(subject_list))
       

        # Append data to lists
        authors.append(author)
        titles.append(title)
        summaries.append(summary)
        languages.append(language)
        

    except AttributeError:
        # Handle cases where data is not found
        authors.append(None)
        titles.append(None)
        summaries.append(None)
        languages.append(None)
        subjects.append(None)
       

# Create a new DataFrame with the scraped data
scraped_data = pd.DataFrame({
    'Author': authors,
    'Title': titles,
    'Summary': summaries,
    'Language': languages,
    'Subject': subjects
})

# Save the new DataFrame to a CSV file
scraped_data.to_csv('scrap/scraped_ebooks.csv', index=False)


In [7]:
books = pd.read_csv("scrap/scraped_ebooks.csv")
books

Author  \
0    Shelley, Mary Wollstonecraft, 1797-1851   
1                    Austen, Jane, 1775-1817   
2            Shakespeare, William, 1564-1616   
3                Melville, Herman, 1819-1891   
4            Hawthorne, Nathaniel, 1804-1864   
..                                       ...   
95            Dostoyevsky, Fyodor, 1821-1881   
96  Barrie, J. M. (James Matthew), 1860-1937   
97                  Salten, Felix, 1869-1945   
98                           Wilhelm, Thomas   
99  Wells, H. G. (Herbert George), 1866-1946   

                                                Title  \
0             Frankenstein; Or, The Modern Prometheus   
1                                 Pride and Prejudice   
2                                    Romeo and Juliet   
3                            Moby Dick; Or, The Whale   
4                                  The Scarlet Letter   
..                                                ...   
95  White Nights and Other StoriesThe Novels of Fy...   
96                                          Peter Pan   
97  Josefine Mutzenbacheroder Die Geschichte einer...   
98  A Military Dictionary and GazetteerComprising ...   
99                                   The Time Machine   

                                              Summary Language  \
0   "Frankenstein; Or, The Modern Prometheus" by M...  English   
1   "Pride and Prejudice" by Jane Austen is a clas...  English   
2   "Romeo and Juliet" by William Shakespeare is a...  English   
3   "Moby Dick; Or, The Whale" by Herman Melville ...  English   
4   "The Scarlet Letter" by Nathaniel Hawthorne is...  English   
..                                                ...      ...   
95  "White Nights and Other Stories" by Fyodor Dos...  English   
96  "Peter and Wendy" by J.M. Barrie is a classic ...  English   
97  "Josefine Mutzenbacher" by Felix Salten is a f...   German   
98  "A Military Dictionary and Gazetteer" by Thoma...  English   
99  "The Time Machine" by H. G. Wells is a science...  English   

                                              Subject  
0   Science fiction, Horror tales, Gothic fiction,...  
1   England -- Fiction, Young women -- Fiction, Lo...  
2   Vendetta -- Drama, Youth -- Drama, Verona (Ita...  
3   Whaling -- Fiction, Sea stories, Psychological...  
4   Adultery -- Fiction, Historical fiction, Reven...  
..                                                ...  
95  Russian fiction -- Translations into English, ...  
96  Fantasy literature, Peter Pan (Fictitious char...  
97                   Erotic stories, Austrian fiction  
98  Naval art and science -- Dictionaries, Militar...  
99  Science fiction, Time travel -- Fiction, Dysto...  

[100 rows x 5 columns]

In [12]:
import requests
from bs4 import BeautifulSoup
import pandas as pd
import os

# URL à scraper
url = "https://gutenberg.org/ebooks/bookshelf/"

# Faire la requête HTTP
response = requests.get(url)
soup = BeautifulSoup(response.content, "html.parser")

# Trouver le <div> contenant les livres
bookshelves_div = soup.find("div", class_="bookshelves")

# Préparer une liste pour les données à sauvegarder dans le CSV
data = []

# Trouver tous les éléments <a> dans le <div> des bookshelves
for ul in bookshelves_div.find_all("ul"):
    for item in ul.find_all("li"):
        link_tag = item.find("a")
        if link_tag:  # Vérifier si <a> existe
            category = link_tag.text.strip()  # Titre de la catégorie
            link = link_tag["href"]  # Lien
            # Ajouter les données à la liste
            data.append({"Category": category, "Link": link})

# Créer un DataFrame à partir des données
df = pd.DataFrame(data)

# Définir le chemin du fichier CSV
folder_path = "scrap"
csv_file = "categories_links.csv"
csv_path = os.path.join(folder_path, csv_file)

# Créer le dossier scrap s'il n'existe pas
os.makedirs(folder_path, exist_ok=True)

# Sauvegarder le DataFrame dans un fichier CSV
df.to_csv(csv_path, index=False)

print(f"Données sauvegardées avec succès dans : {csv_path}")


Données sauvegardées avec succès dans : scrap\categories_links.csv


In [13]:
category = pd.read_csv("scrap/categories_links.csv")
category

Category  \
0                                Animal   
1                      Canada Bookshelf   
2                  Children's Bookshelf   
3                    Classics Bookshelf   
4                   Countries Bookshelf   
5                       Crime Bookshelf   
6                   Education Bookshelf   
7                          Emmy's Picks   
8                     Fiction Bookshelf   
9                   Fine arts Bookshelf   
10              General Works Bookshelf   
11                  Geography Bookshelf   
12                    History Bookshelf   
13    Language and Literature Bookshelf   
14                        Law Bookshelf   
15                      Music Bookshelf   
16  Psychology and Philosophy Bookshelf   
17                   Religion Bookshelf   
18                    Science Bookshelf   
19            Social Sciences Bookshelf   
20                 Technology Bookshelf   
21                       Wars Bookshelf   

                                                 Link  
0            /ebooks/bookshelves/search/?query=animal  
1            /ebooks/bookshelves/search/?query=canada  
2   /ebooks/bookshelves/search/?query=children%7Cc...  
3          /ebooks/bookshelves/search/?query=classics  
4   /ebooks/bookshelves/search/?query=africa.%7CAr...  
5   /ebooks/bookshelves/search/?query=crime%7Cdete...  
6         /ebooks/bookshelves/search/?query=education  
7                             /ebooks/bookshelf/emmys  
8   /ebooks/bookshelves/search/?query=fiction%7Cad...  
9   /ebooks/bookshelves/search/?query=architecture...  
10        /ebooks/bookshelves/search/?query=reference  
11  /ebooks/bookshelves/search/?query=africa.%7CAn...  
12  /ebooks/bookshelves/search/?query=history%7CAr...  
13  /ebooks/bookshelves/search/?query=language%7Cl...  
14  /ebooks/bookshelves/search/?query=law%7CNotewo...  
15    /ebooks/bookshelves/search/?query=music%7Copera  
16  /ebooks/bookshelves/search/?query=Bibliomania%...  
17  /ebooks/bookshelves/search/?query=Atheism%20%7...  
18  /ebooks/bookshelves/search/?query=Astronomy%20...  
19  /ebooks/bookshelves/search/?query=Anarchism%20...  
20  /ebooks/bookshelves/search/?query=technology%2...  
21              /ebooks/bookshelves/search/?query=war

In [24]:
import requests
from bs4 import BeautifulSoup
import pandas as pd
import os

# Charger le fichier CSV contenant les liens
csv_input_path = "scrap/categories_links.csv"
df_links = pd.read_csv(csv_input_path)

# Liste pour stocker les données extraites
books_data = []

# Boucle à travers chaque lien du CSV
for index, row in df_links.iterrows():
    link = f"https://gutenberg.org{row['Link']}"  # Concaténer l'URL de base avec le lien
    print(f"Scraping {link}...")
    
    response = requests.get(link)
    soup = BeautifulSoup(response.content, "html.parser")
    
    # Trouver tous les éléments <li class="navlink">
    for li in soup.find_all("li", class_="navlink"):
        a_tag = li.find("a", class_="link")
        if a_tag:  # Vérifier si <a> existe
            title = a_tag.find("span", class_="title").text.strip()  # Titre
            link = a_tag["href"]  # Lien
            books_data.append({"Link": link, "Title": title})

# Créer un DataFrame à partir des données
df_books = pd.DataFrame(books_data)

# Définir le chemin du fichier CSV de sortie
books_csv_path = "scrap/books.csv"

# Sauvegarder le DataFrame dans un fichier CSV
df_books.to_csv(books_csv_path, index=False)

print(f"Données des livres sauvegardées avec succès dans : {books_csv_path}")


Scraping https://gutenberg.org/ebooks/bookshelves/search/?query=animal...
Scraping https://gutenberg.org/ebooks/bookshelves/search/?query=canada...
Scraping https://gutenberg.org/ebooks/bookshelves/search/?query=children%7Cchristmas%7Cchild%7Cschool...
Scraping https://gutenberg.org/ebooks/bookshelves/search/?query=classics...
Scraping https://gutenberg.org/ebooks/bookshelves/search/?query=africa.%7CArgentina.%7CAustralia%7CBulgaria%7CCanada%7CCzech%7Cegypt%7Cfrance.%7Cgermany.%7Cgreece.%7Cindia%7Citaly%7Czealand%7Cnorway%7Csouth%20america%7C.travel.%7CUnited%20Kingdom%7C.united%20states.!law...
Scraping https://gutenberg.org/ebooks/bookshelves/search/?query=crime%7Cdetective%7Cmystery...
Scraping https://gutenberg.org/ebooks/bookshelves/search/?query=education...
Scraping https://gutenberg.org/ebooks/bookshelf/emmys...
Scraping https://gutenberg.org/ebooks/bookshelves/search/?query=fiction%7Cadventure%7Cfantasy%7Chumor%7Chorror%7Cwestern...
Scraping https://gutenberg.org/ebooks/booksh

In [28]:
df = pd.read_csv("scrap/books.csv")
df

Link  \
0    /ebooks/bookshelves/search/?query=animal&sort_...   
1    /ebooks/bookshelves/search/?query=animal&sort_...   
2    /ebooks/bookshelves/search/?query=animal&sort_...   
3                                /ebooks/bookshelf/150   
4                                /ebooks/bookshelf/151   
..                                                 ...   
275                              /ebooks/bookshelf/137   
276                              /ebooks/bookshelf/196   
277                              /ebooks/bookshelf/140   
278                              /ebooks/bookshelf/139   
279                              /ebooks/bookshelf/281   

                            Title  
0    Sort Alphabetically by Title  
1                Sort by Quantity  
2            Sort by Release Date  
3                          Animal  
4                Animals-Domestic  
..                            ...  
275                      Boer War  
276    American Revolutionary War  
277          Spanish American War  
278             English Civil War  
279      The Illustrated War News  

[280 rows x 2 columns]

In [30]:
import pandas as pd
import requests
from bs4 import BeautifulSoup

# Charger le fichier CSV
df = pd.read_csv('scrap/books.csv')

# Liste pour stocker les résultats
results = []

# Parcourir chaque lien dans la colonne 'Link'
for link in df['Link']:
    # Ajouter le préfixe au lien
    full_link = f'https://gutenberg.org{link}'
    
    # Afficher le lien que vous scrappez
    print(f'Scraping link: {full_link}')
    
    # Faire une requête HTTP pour chaque lien
    response = requests.get(full_link)
    
    # Vérifier si la requête a réussi
    if response.status_code == 200:
        soup = BeautifulSoup(response.content, 'html.parser')
        
        # Trouver tous les éléments <li class="navlink">
        navlinks = soup.find_all('li', class_='navlink')
        
        # Extraire le title et le href de chaque navlink
        for navlink in navlinks:
            a_tag = navlink.find('a', class_='link')
            title = a_tag.find('span', class_='title').text.strip() if a_tag else None
            href = a_tag['href'] if a_tag else None
            
            # Ajouter les résultats à la liste
            if title and href:
                results.append({'Title': title, 'Link': href})

# Convertir les résultats en DataFrame
results_df = pd.DataFrame(results)

# Sauvegarder les résultats dans un nouveau fichier CSV
results_df.to_csv('scrap/books_details.csv', index=False)


Scraping link: https://gutenberg.org/ebooks/bookshelves/search/?query=animal&sort_order=alpha
Scraping link: https://gutenberg.org/ebooks/bookshelves/search/?query=animal&sort_order=quantity
Scraping link: https://gutenberg.org/ebooks/bookshelves/search/?query=animal&sort_order=release_date
Scraping link: https://gutenberg.org/ebooks/bookshelf/150
Scraping link: https://gutenberg.org/ebooks/bookshelf/151
Scraping link: https://gutenberg.org/ebooks/bookshelf/154
Scraping link: https://gutenberg.org/ebooks/bookshelf/156
Scraping link: https://gutenberg.org/ebooks/bookshelf/152
Scraping link: https://gutenberg.org/ebooks/bookshelf/155
Scraping link: https://gutenberg.org/ebooks/bookshelf/153
Scraping link: https://gutenberg.org/ebooks/bookshelf/157
Scraping link: https://gutenberg.org/ebooks/bookshelf/118
Scraping link: https://gutenberg.org/ebooks/search/?query=dp-canada
Scraping link: https://gutenberg.org/ebooks/search/?query=canadas
Scraping link: https://gutenberg.org/ebooks/bookshel

In [31]:
links = pd.read_csv("scrap/books_details.csv")
links

Title  \
0                Sort by Popularity   
1                  Sort by Quantity   
2              Sort by Release Date   
3                            Animal   
4                  Animals-Domestic   
...                             ...   
1484  Sort Alphabetically by Author   
1485           Sort by Release Date   
1486   Sort Alphabetically by Title   
1487  Sort Alphabetically by Author   
1488           Sort by Release Date   

                                                   Link  
0     /ebooks/bookshelves/search/?query=animal&sort_...  
1     /ebooks/bookshelves/search/?query=animal&sort_...  
2     /ebooks/bookshelves/search/?query=animal&sort_...  
3                                 /ebooks/bookshelf/150  
4                                 /ebooks/bookshelf/151  
...                                                 ...  
1484            /ebooks/bookshelf/139?sort_order=author  
1485      /ebooks/bookshelf/139?sort_order=release_date  
1486             /ebooks/bookshelf/281?sort_order=title  
1487            /ebooks/bookshelf/281?sort_order=author  
1488      /ebooks/bookshelf/281?sort_order=release_date  

[1489 rows x 2 columns]

In [32]:
import pandas as pd
import requests
from bs4 import BeautifulSoup

# Load the CSV file containing links
df = pd.read_csv('scrap/premieres_5000_lignes.csv')

# Initialize the lists to store data
authors = []
titles = []
summaries = []
languages = []
subjects = []

# Iterate through each link in the DataFrame
for index, row in df.iterrows():
    link = row['Link']
    
    # Create the full link
    full_link = f'https://gutenberg.org{link}'

    response = requests.get(full_link)
    soup = BeautifulSoup(response.content, 'html.parser')

    # Extract the required fields
    try:
        author = soup.find('th', string='Author').find_next('td').get_text(strip=True)
        title = soup.find('th', string='Title').find_next('td').get_text(strip=True)
        summary = soup.find('th', string='Summary').find_next('td').get_text(strip=True)
        language = soup.find('th', string='Language').find_next('td').get_text(strip=True)
        subject_tags = soup.find_all('th', string='Subject')
        subject_list = [tag.find_next('td').get_text(strip=True) for tag in subject_tags]
        subjects.append(", ".join(subject_list))

        # Append data to lists
        authors.append(author)
        titles.append(title)
        summaries.append(summary)
        languages.append(language)

    except AttributeError:
        # Handle cases where data is not found
        authors.append(None)
        titles.append(None)
        summaries.append(None)
        languages.append(None)
        subjects.append(None)

# Create a new DataFrame with the scraped data
scraped_data = pd.DataFrame({
    'Author': authors,
    'Title': titles,
    'Summary': summaries,
    'Language': languages,
    'Subject': subjects
})

# Save the new DataFrame to a CSV file
scraped_data.to_csv('scrap/scraped_books.csv', index=False)


print('Scraping terminé ! Les résultats ont été sauvegardés dans books_final_details.csv.')


Scraping link: https://gutenberg.org/ebooks/bookshelves/search/?query=animal&sort_order=downloads
Scraping link: https://gutenberg.org/ebooks/bookshelves/search/?query=animal&sort_order=quantity
Scraping link: https://gutenberg.org/ebooks/bookshelves/search/?query=animal&sort_order=release_date
Scraping link: https://gutenberg.org/ebooks/bookshelf/150
Scraping link: https://gutenberg.org/ebooks/bookshelf/151
Scraping link: https://gutenberg.org/ebooks/bookshelf/152
Scraping link: https://gutenberg.org/ebooks/bookshelf/154
Scraping link: https://gutenberg.org/ebooks/bookshelf/155
Scraping link: https://gutenberg.org/ebooks/bookshelf/156
Scraping link: https://gutenberg.org/ebooks/bookshelf/157
Scraping link: https://gutenberg.org/ebooks/bookshelf/153
Scraping link: https://gutenberg.org/ebooks/bookshelves/search/?query=animal&sort_order=downloads
Scraping link: https://gutenberg.org/ebooks/bookshelves/search/?query=animal&sort_order=alpha
Scraping link: https://gutenberg.org/ebooks/book

In [34]:
df = pd.read_csv("scrap/books_final_details.csv")
df

Title           Link
0                The Extermination of the American Bison  /ebooks/17748
1      Birds, Illustrated by Color Photography, Vol. ...  /ebooks/25983
2                 Argentine Ornithology, Volume 1 (of 2)  /ebooks/38956
3      Metabolic Adaptation to Climate and Distributi...  /ebooks/36036
4      Birds, Illustrated by Color Photography, Vol. ...  /ebooks/30221
...                                                  ...            ...
26409     Illustrated War News, Number 21, Dec. 30, 1914  /ebooks/18334
26410  The Illustrated War News, Number 15, Nov. 18, ...  /ebooks/18333
26411  The Illustrated War News, Number 21, Dec. 30, ...  /ebooks/18334
26412  The Illustrated War News, Number 21, Dec. 30, ...  /ebooks/18334
26413  The Illustrated War News, Number 15, Nov. 18, ...  /ebooks/18333

[26414 rows x 2 columns]

In [35]:
# Sélectionner les premières 5000 lignes
df_subset = df.head(5000)

# Sauvegarder dans un fichier CSV
df_subset.to_csv('scrap/premieres_5000_lignes.csv', index=False)  

In [37]:
import pandas as pd
import requests
from bs4 import BeautifulSoup

# Load the CSV file containing links
df = pd.read_csv('scrap/premieres_5000_lignes.csv')

# Initialize the lists to store data
authors = []
titles = []
summaries = []
languages = []
subjects = []

# Iterate through each link in the DataFrame
for index, row in df.iterrows():
    link = row['Link']
    
    # Create the full link
    full_link = f'https://gutenberg.org{link}'

    response = requests.get(full_link)
    soup = BeautifulSoup(response.content, 'html.parser')

    # Extract the required fields
    try:
        author = soup.find('th', string='Author').find_next('td').get_text(strip=True)
        title = soup.find('th', string='Title').find_next('td').get_text(strip=True)
        summary = soup.find('th', string='Summary').find_next('td').get_text(strip=True)
        language = soup.find('th', string='Language').find_next('td').get_text(strip=True)
        subject_tags = soup.find_all('th', string='Subject')
        subject_list = [tag.find_next('td').get_text(strip=True) for tag in subject_tags]
        subjects.append(", ".join(subject_list))

        # Append data to lists
        authors.append(author)
        titles.append(title)
        summaries.append(summary)
        languages.append(language)

        # Print the scraped data
        print(f"Scraped {index + 1}:")
        print(f"  Link: {full_link}")
        print(f"  Author: {author}")
        print(f"  Title: {title}")
        print(f"  Summary: {summary}")
        print(f"  Language: {language}")
        print(f"  Subjects: {', '.join(subject_list)}")
        print("")

    except AttributeError:
        # Handle cases where data is not found
        authors.append(None)
        titles.append(None)
        summaries.append(None)
        languages.append(None)
        subjects.append(None)

# Create a new DataFrame with the scraped data
scraped_data = pd.DataFrame({
    'Author': authors,
    'Title': titles,
    'Summary': summaries,
    'Language': languages,
    'Subject': subjects
})

# Save the new DataFrame to a CSV file
scraped_data.to_csv('scrap/scraped_books.csv', index=False)


Scraped 1:
  Link: https://gutenberg.org/ebooks/17748
  Author: Hornaday, William T. (William Temple), 1854-1937
  Title: The Extermination of the American Bison
  Summary: "The Extermination of the American Bison" by William T. Hornaday is a historical account written in the late 19th century. This work focuses on the discovery, life history, and near extinction of the American bison, shedding light on both the animal itself and the tragic consequences of human intervention. Hornaday aims to raise awareness about the perils of wanton destruction of wildlife through the story of the bison's decline.  The opening of the book outlines the initial encounters Europeans had with the American bison, starting with Montezuma's menagerie in the 16th century. Hornaday describes how explorers and settlers came across bison in various parts of North America, emphasizing their vast geographical distribution and abundance. The narrative reveals the profound impact of human activity, such as hunting 

In [38]:
df = pd.read_csv("scrap/scraped_books.csv")
df

Author  \
0     Hornaday, William T. (William Temple), 1854-1937   
1                                              Various   
2                    Sclater, Philip Lutley, 1829-1913   
3                                      Mugaas, John N.   
4                                              Various   
...                                                ...   
4995                        Dante Alighieri, 1265-1321   
4996                        Dante Alighieri, 1265-1321   
4997                        Dante Alighieri, 1265-1321   
4998                        Dante Alighieri, 1265-1321   
4999                           Ruskin, John, 1819-1900   

                                                  Title  \
0               The Extermination of the American Bison   
1     Birds, Illustrated by Color Photography, Vol. ...   
2     Argentine Ornithology, Volume 1 (of 2)A descri...   
3     Metabolic Adaptation to Climate and Distributi...   
4     Birds, Illustrated by Color Photography, Vol. ...   
...                                                 ...   
4995                       The New Life (La Vita Nuova)   
4996  Divine Comedy, Longfellow's Translation, Complete   
4997  The Divine Comedy by Dante, Illustrated, Purga...   
4998  The vision of hell.By Dante Alighieri.Translat...   
4999              The Stones of Venice, Volume 1 (of 3)   

                                                Summary Language  \
0     "The Extermination of the American Bison" by W...  English   
1     "Birds, Illustrated by Color Photography, Vol....  English   
2     "Argentine Ornithology, Volume 1 (of 2)" by Ph...  English   
3     "Metabolic Adaptation to Climate and Distribut...  English   
4     "Birds, Illustrated by Color Photography, Vol....  English   
...                                                 ...      ...   
4995  "The New Life (La Vita Nuova)" by Dante Alighi...  English   
4996  "Divine Comedy, Longfellow's Translation, Comp...  English   
4997  "The Divine Comedy" by Dante Alighieri is an e...  English   
4998  "The Vision of Hell" by Dante Alighieri is an ...  English   
4999  "The Stones of Venice, Volume 1" by John Ruski...  English   

                                                Subject  
0     American bison, Wildlife conservation -- Unite...  
1     Zoological illustration -- Periodicals, Birds ...  
2                                    Birds -- Argentina  
3     Raccoon -- Metabolism -- Climatic factors, Pro...  
4     Zoological illustration -- Periodicals, Birds ...  
...                                                 ...  
4995    Italian literature -- Translations into English  
4996  Epic poetry, Italian -- Translations into Engl...  
4997  Epic poetry, Italian -- Translations into Engl...  
4998  Hell -- Poetry, Epic poetry, Italian -- Transl...  
4999                    Architecture -- Italy -- Venice  

[5000 rows x 5 columns]